In [1]:
import ast
import csv
import json
import reverse_geocoder as rg

import numpy as np
import pandas as pd

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

# FAIRsharing

In [2]:
fairsharing_df = pd.read_csv('../data/raw/FAIRsharingDBrec_summary20210304.csv', 
                             delimiter='|', header=0,
                             names=['full_name', 'short_name', 'fs_url', 'url', 'countries', 'subjects'])
fairsharing_df['subjects'] = fairsharing_df.subjects.str.split(pat=',')
fairsharing_df['countries'] = fairsharing_df.countries.str.split(pat=',')
fairsharing_df.head()

full_name  short_name  \
0                                            GenBank     GenBank   
1                                          GlycoNAVI   GlycoNAVI   
2                                           ADHDgene    ADHDgene   
3  Allele frequency resource for research and tea...      ALFRED   
4               Animal Transcription Factor Database  AnimalTFDB   

                                              fs_url  \
0  https://fairsharing.org/10.25504/FAIRsharing.9...   
1  https://fairsharing.org/10.25504/FAIRsharing.w...   
2  https://fairsharing.org/10.25504/FAIRsharing.m...   
3  https://fairsharing.org/10.25504/FAIRsharing.y...   
4  https://fairsharing.org/10.25504/FAIRsharing.e...   

                                           url  \
0        https://www.ncbi.nlm.nih.gov/genbank/   
1                       https://glyconavi.org/   
2                     http://adhd.psych.ac.cn/   
3                   http://alfred.med.yale.edu   
4  http://bioinfo.life.hust.edu.cn/AnimalTFDB/   

                                countries  \
0  [European Union, Japan, United States]   
1                                 [Japan]   
2                                 [China]   
3                         [United States]   
4                                 [China]   

                                            subjects  
0  [Bioinformatics, Data Management, Data Submiss...  
1  [Chemistry, Glycomics, Life Science, Organic C...  
2                     [Biomedical Science, Genetics]  
3                                     [Life Science]  
4                                     [Life Science]

In [3]:
fairsharing_df.describe()

full_name short_name  \
count                               1752       1752   
unique                              1752       1741   
top     The Cardiovascular Research Grid        CGD   
freq                                   1          3   

                                     fs_url                        url  \
count                                  1752                       1752   
unique                                 1752                       1752   
top     https://fairsharing.org/bsg-d001750  http://www.bmrb.wisc.edu/   
freq                                      1                          1   

              countries        subjects  
count              1749            1690  
unique              178             834  
top     [United States]  [Life Science]  
freq                588             367

In [4]:
fairsharing_subjects = fairsharing_df.explode('subjects').groupby('subjects')[['url']].count().sort_values('url', ascending=False)

data = [
    go.Bar(
        x=fairsharing_subjects.index,
        y=fairsharing_subjects['url']
    )
]

layout = go.Layout(
    title='Fairsharing subject coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [5]:
fairsharing_countries = fairsharing_df.explode('countries').groupby('countries')[['url']].count().sort_values('url', ascending=False)

data = [
    go.Bar(
        x=fairsharing_countries.index,
        y=fairsharing_countries['url']
    )
]

layout = go.Layout(
    title='Fairsharing country coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

# re3data

In [6]:
re3data_df = pd.read_csv('../data/raw/re3data_opendoar.csv')
re3data_df = re3data_df[re3data_df.id.str.contains('re3data')]
re3data_df.head()

id  \
4   10|re3data_____::3f2e20af26ead0432f5470d8b739638d   
7   10|re3data_____::e1db3f9d2fa6c8d8067bc471ab50bdfc   
13  10|re3data_____::59521daca59ac29b811343cc4cd370cf   
14  10|re3data_____::ec1ba1674c852466c266acb64c618d15   
19  10|re3data_____::2ada591fb1bc9aee72a6d3e0c1ae8a76   

                                                  url  \
4                    http://planttfdb.cbi.pku.edu.cn/   
7                         https://spdf.gsfc.nasa.gov/   
13                         http://card.westgis.ac.cn/   
14                     https://www.psycharchives.org/   
19  https://www.ihfc-iugg.org/products/global-heat...   

                                        official_name  \
4                 Plant Transcription Factor Database   
7                         Space Physics Data Facility   
13  Cold and Arid Regions Science Data Center at L...   
14                                      Psycharchives   
19  The Global Heat Flow Database of the Internati...   

                                         english_name description  latitude  \
4                                           PlantTFDB         NaN       0.0   
7             NASA's Space Physics Data Facility SPDF         NaN       0.0   
13  CARD WDC for Glaciology and Geocryology World ...         NaN       0.0   
14                                                NaN         NaN       0.0   
19                   International Heat-flow Database         NaN       0.0   

    longitude                                           subjects  
4         0.0  ['Life Sciences', 'Basic Biological and Medica...  
7         0.0  ['Natural Sciences', 'Astrophysics and Astrono...  
13        0.0  ['Natural Sciences', 'Geosciences (including G...  
14        0.0  ['Humanities and Social Sciences', 'Psychology...  
19        0.0  ['Natural Sciences', 'Geology and Palaeontolog...

In [7]:
re3data_df.loc[(re3data_df.latitude == 0.0) & (re3data_df.longitude == 0.0), ['latitude', 'longitude']] = [np.nan, np.nan]

In [8]:
re3data_df.subjects

4       ['Life Sciences', 'Basic Biological and Medica...
7       ['Natural Sciences', 'Astrophysics and Astrono...
13      ['Natural Sciences', 'Geosciences (including G...
14      ['Humanities and Social Sciences', 'Psychology...
19      ['Natural Sciences', 'Geology and Palaeontolog...
                              ...                        
8693    ['Life Sciences', 'Basic Biological and Medica...
8695    ['Natural Sciences', 'Atmospheric Science and ...
8697    ['Natural Sciences', 'Atmospheric Science and ...
8699    ['Natural Sciences', 'Atmospheric Science and ...
8705    ['Life Sciences', 'Plant Sciences', 'Plant Gen...
Name: subjects, Length: 2693, dtype: object

In [9]:
re3data_df['subjects'] = re3data_df.subjects.apply(lambda x: ast.literal_eval(x))

In [10]:
def merge_lists(lists):
    res = []
    for l in lists:
        res = res + l
    return res

re3data_cleaned_subjects = re3data_df.explode('subjects').subjects.str.split(',| and ', expand=True)\
                                .apply(lambda row: row.dropna().tolist(), axis=1)\
                                .reset_index()\
                                .groupby('index')[0].apply(lambda x: merge_lists(x))

In [11]:
re3data_cleaned_subjects

index
4       [Life Sciences, Basic Biological, Medical Rese...
7       [Natural Sciences, Astrophysics, Astronomy, Ph...
13      [Natural Sciences, Geosciences (including Geog...
14      [Humanities, Social Sciences, Psychology, Soci...
19      [Natural Sciences, Geology, Palaeontology, Geo...
                              ...                        
8693    [Life Sciences, Basic Biological, Medical Rese...
8695    [Natural Sciences, Atmospheric Science, Oceano...
8697    [Natural Sciences, Atmospheric Science, Oceano...
8699    [Natural Sciences, Atmospheric Science, Oceano...
8705    [Life Sciences, Plant Sciences, Plant Genetics...
Name: 0, Length: 2693, dtype: object

In [12]:
re3data_df = re3data_df.join(re3data_cleaned_subjects)

In [13]:
re3data_df.drop(columns=['subjects'], inplace=True)
re3data_df.rename(columns={0:'subjects'}, inplace=True)

In [14]:
re3data_df.describe(include='all')

id  \
count                                                2693   
unique                                               2693   
top     10|re3data_____::e59f89142e8d47d32523c53a9137f07b   
freq                                                    1   
mean                                                  NaN   
std                                                   NaN   
min                                                   NaN   
25%                                                   NaN   
50%                                                   NaN   
75%                                                   NaN   
max                                                   NaN   

                                  url  official_name  \
count                            2673           2693   
unique                           2661           2668   
top     http://iubio.bio.indiana.edu/  IUBio-Archive   
freq                                2              2   
mean                              NaN            NaN   
std                               NaN            NaN   
min                               NaN            NaN   
25%                               NaN            NaN   
50%                               NaN            NaN   
75%                               NaN            NaN   
max                               NaN            NaN   

                    english_name  \
count                       2034   
unique                      2010   
top     Research Data Repository   
freq                           2   
mean                         NaN   
std                          NaN   
min                          NaN   
25%                          NaN   
50%                          NaN   
75%                          NaN   
max                          NaN   

                                              description    latitude  \
count                                                  38    5.000000   
unique                                                 38         NaN   
top     IUBio Archive is an archive of biology data an...         NaN   
freq                                                    1         NaN   
mean                                                  NaN   61.668113   
std                                                   NaN   96.984457   
min                                                   NaN   12.123000   
25%                                                   NaN   12.123000   
50%                                                   NaN   12.123400   
75%                                                   NaN   37.971163   
max                                                   NaN  234.000000   

         longitude                                           subjects  
count     5.000000                                               2693  
unique         NaN                                               1427  
top            NaN  [Humanities, Social Sciences, Life Sciences, N...  
freq           NaN                                                209  
mean     36.623678                                                NaN  
std      48.547521                                                NaN  
min      12.123000                                                NaN  
25%      12.123400                                                NaN  
50%      12.123400                                                NaN  
75%      23.748590                                                NaN  
max     123.000000                                                NaN

In [15]:
re3data_subjects = re3data_df.explode('subjects').groupby('subjects')[['url']].count().sort_values('url', ascending=False)

data = [
    go.Bar(
        x=re3data_subjects.index,
        y=re3data_subjects['url']
    )
]

layout = go.Layout(
    title='re3data subject coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

# OpenDOAR

In [82]:
opendoar_df = pd.read_csv('../data/raw/re3data_opendoar.csv')
opendoar_df = opendoar_df[opendoar_df.id.str.contains('opendoar')]
opendoar_df.head()

id  \
0  10|opendoar____::e833e042f509c996b1b25324d56659fb   
1  10|opendoar____::f621585df244e9596dc70a39b579efb1   
2  10|opendoar____::437d7d1d97917cd627a34a6a0fb41136   
3  10|opendoar____::d840cc5d906c3e9c84374c8919d2074e   
5  10|opendoar____::4ba3c163cd1efd4c14e3a415fa0a3010   

                                                 url  \
0                          http://www.bilbao.net/bld   
1       https://researchdirect.westernsydney.edu.au/   
2         http://redress.lancs.ac.uk/Learning_Space/   
3  http://digitallibrary.usc.edu/search/controlle...   
5                 http://www.ufgd.edu.br:8080/jspui/   

                                       official_name  \
0                  BLD - Bilboko Liburutegi Digitala   
1                      Western Sydney ResearchDirect   
2                           Learning Space Catalogue   
3                                USC Digital Library   
5  Repositório de Divulgação das Produções Cientí...   

                                        english_name  \
0                  BLD - Bilboko Liburutegi Digitala   
1                      Western Sydney ResearchDirect   
2                                                NaN   
3                                USC Digital Library   
5  Repositório de Divulgação das Produções Cientí...   

                                         description   latitude   longitude  \
0  BLD is a repository of digital documents, desi...  43.256699   -2.924100   
1                                                NaN   0.000000    0.000000   
2  This repository is a Social Science e-Science ...  54.010760   -2.784990   
3  This is an institutional repository providing ...  34.052200 -118.242996   
5  This site provides access to the research outp... -22.221800  -54.806400   

                                            subjects  
0                                                 []  
1                                                 []  
2  ['Social Sciences General', 'Science General',...  
3                                                 []  
5                                                 []

In [84]:
opendoar_df.subjects

0                                                      []
1                                                      []
2       ['Social Sciences General', 'Science General',...
3                                                      []
5                                                      []
                              ...                        
8701                                ['Multidisciplinary']
8702                                                   []
8703                           ['Business and Economics']
8704    ['Earth and Planetary Sciences', 'Ecology and ...
8706                                                   []
Name: subjects, Length: 6014, dtype: object

In [85]:
opendoar_df['subjects'] = opendoar_df.subjects.apply(lambda x: ast.literal_eval(x))

In [86]:
opendoar_cleaned_subjects = opendoar_df.explode('subjects').subjects.str.split(',| and ', expand=True)\
                                .apply(lambda row: row.dropna().tolist(), axis=1)\
                                .reset_index()\
                                .groupby('index')[0].apply(lambda x: merge_lists(x))

In [87]:
opendoar_cleaned_subjects

index
0                                                      []
1                                                      []
2       [Social Sciences General, Science General, Com...
3                                                      []
5                                                      []
                              ...                        
8701                                  [Multidisciplinary]
8702                                                   []
8703                                [Business, Economics]
8704    [Earth, Planetary Sciences, Ecology, Environme...
8706                                                   []
Name: 0, Length: 6014, dtype: object

In [88]:
opendoar_df = opendoar_df.join(opendoar_cleaned_subjects)

In [89]:
opendoar_df.drop(columns=['subjects'], inplace=True)
opendoar_df.rename(columns={0: 'subjects'}, inplace=True)

In [90]:
opendoar_df.describe(include='all')

id  \
count                                                6014   
unique                                               6014   
top     10|opendoar____::a2557a7b2e94197ff767970b67041697   
freq                                                    1   
mean                                                  NaN   
std                                                   NaN   
min                                                   NaN   
25%                                                   NaN   
50%                                                   NaN   
75%                                                   NaN   
max                                                   NaN   

                                       url  \
count                                 6013   
unique                                5953   
top     http://harp.lib.hiroshima-u.ac.jp/   
freq                                     3   
mean                                   NaN   
std                                    NaN   
min                                    NaN   
25%                                    NaN   
50%                                    NaN   
75%                                    NaN   
max                                    NaN   

                                 official_name english_name  \
count                                     6014         5500   
unique                                    5946         5413   
top     Hiroshima Associated Repository Portal         AURA   
freq                                         3            4   
mean                                       NaN          NaN   
std                                        NaN          NaN   
min                                        NaN          NaN   
25%                                        NaN          NaN   
50%                                        NaN          NaN   
75%                                        NaN          NaN   
max                                        NaN          NaN   

                                              description      latitude  \
count                                                5776   6014.000000   
unique                                               4920           NaN   
top     This site provides access to the research outp...           NaN   
freq                                                   98           NaN   
mean                                                  NaN     38.649393   
std                                                   NaN    788.406173   
min                                                   NaN    -79.029999   
25%                                                   NaN      4.644632   
50%                                                   NaN     37.930449   
75%                                                   NaN     47.294400   
max                                                   NaN  61138.800781   

          longitude subjects  
count   6014.000000     6014  
unique          NaN      201  
top             NaN       []  
freq            NaN     5273  
mean       7.810948      NaN  
std       71.689788      NaN  
min     -683.103027      NaN  
25%      -49.273300      NaN  
50%        4.788870      NaN  
75%       30.685501      NaN  
max      178.438995      NaN

In [91]:
opendoar_subjects = opendoar_df.explode('subjects').groupby('subjects')[['url']].count().sort_values('url', ascending=False)

data = [
    go.Bar(
        x=opendoar_subjects.index,
        y=opendoar_subjects['url']
    )
]

layout = go.Layout(
    title='OpenDOAR subject coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [92]:
reverse_geocoding = pd.DataFrame(rg.search(opendoar_df[['latitude', 'longitude']].apply(tuple, axis=1).tolist()))
reverse_geocoding['lat'] = reverse_geocoding['lat'].astype('float')
reverse_geocoding['lon'] = reverse_geocoding['lon'].astype('float')
reverse_geocoding

lat        lon         name              admin1  \
0     43.26271   -2.92528       Bilbao      Basque Country   
1      4.88447   -1.75536     Takoradi             Western   
2     53.98333   -2.78333      Galgate             England   
3     34.05223 -118.24368  Los Angeles          California   
4    -22.22111  -54.80556     Dourados  Mato Grosso do Sul   
...        ...        ...          ...                 ...   
6009  40.85631   14.24641       Napoli            Campania   
6010  38.19394   15.55256      Messina              Sicily   
6011  54.32133   10.13489         Kiel  Schleswig-Holstein   
6012  43.40785  -73.25955    Granville            New York   
6013  33.96095  -83.37794       Athens             Georgia   

                   admin2  cc  
0                 Bizkaia  ES  
1                          GH  
2              Lancashire  GB  
3      Los Angeles County  US  
4                Dourados  BR  
...                   ...  ..  
6009  Provincia di Napoli  IT  
6010              Messina  IT  
6011                       DE  
6012    Washington County  US  
6013        Clarke County  US  

[6014 rows x 6 columns]

In [94]:
opendoar_df = opendoar_df.join(reverse_geocoding[['cc']])

In [96]:
opendoar_df.loc[(opendoar_df.latitude == 0.0) & (opendoar_df.longitude == 0.0), ['latitude', 'longitude', 'cc']] = [np.nan, np.nan, np.nan]


In [103]:
opendoar_countries = opendoar_df.groupby('cc')[['id']].count().sort_values('id', ascending=False)

data = [
    go.Bar(
        x=opendoar_countries.index,
        y=opendoar_countries['id']
    )
]

layout = go.Layout(
    title='OpenDOAR country coverage',
    xaxis=dict(tickangle=45, tickfont=dict(size=12))
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)